In [1]:
# !rm -rf WGAN
# !rm -rf WGAN.zip
!unzip WGAN.zip
!pip install pot

Archive:  WGAN.zip
   creating: WGAN/
  inflating: WGAN/Losses.py          
  inflating: WGAN/NNs.py             
  inflating: WGAN/utils.py           
   creating: WGAN/__pycache__/
  inflating: WGAN/__pycache__/Losses.cpython-37.pyc  
  inflating: WGAN/__pycache__/NNs.cpython-37.pyc  
  inflating: WGAN/__pycache__/utils.cpython-37.pyc  
     |████████████████████████████████| 440kB 7.1MB/s 


In [1]:
from WGAN.NNs import DiscriminatorMLP, DiscriminatorConvNet
from WGAN.utils import divide_by_classes, Trainer, get_gt_wass
from WGAN.Losses import GPLoss, WCLoss, WeightClipper, CEpsilonLoss, CLoss, LPLoss

In [2]:
import torch
import torchvision.transforms as transforms
import torchvision
import torchvision.datasets as datasets
import torchvision.utils as vutils

from torch.autograd import Variable
import torch.autograd as autograd

import torch.nn as nn
import torch.nn.functional as F
import torch

import numpy as np
from tqdm.notebook import tqdm

from itertools import product

In [3]:
cuda = True if torch.cuda.is_available() else False
device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")

In [4]:
transform = transforms.Compose(
    [
    transforms.ToTensor(),
    transforms.Normalize((0.1307,), (0.3081,)),
    transforms.Resize((32, 32)),
    ]
)

In [5]:
!wget www.di.ens.fr/~lelarge/MNIST.tar.gz
!tar -zxvf MNIST.tar.gz

import MNIST

--2021-03-23 21:31:57--  http://www.di.ens.fr/~lelarge/MNIST.tar.gz
Resolving www.di.ens.fr (www.di.ens.fr)... 129.199.99.14
Connecting to www.di.ens.fr (www.di.ens.fr)|129.199.99.14|:80... connected.
HTTP request sent, awaiting response... 302 Found
Location: https://www.di.ens.fr/~lelarge/MNIST.tar.gz [following]
--2021-03-23 21:31:57--  https://www.di.ens.fr/~lelarge/MNIST.tar.gz
Connecting to www.di.ens.fr (www.di.ens.fr)|129.199.99.14|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: unspecified [application/x-gzip]
Saving to: ‘MNIST.tar.gz.1’

MNIST.tar.gz.1          [             <=>    ]  33.20M  11.4MB/s    in 2.9s    

2021-03-23 21:32:01 (11.4 MB/s) - ‘MNIST.tar.gz.1’ saved [34813078]

MNIST/
MNIST/raw/
MNIST/raw/train-labels-idx1-ubyte
MNIST/raw/t10k-labels-idx1-ubyte.gz
MNIST/raw/t10k-labels-idx1-ubyte
MNIST/raw/t10k-images-idx3-ubyte.gz
MNIST/raw/train-images-idx3-ubyte
MNIST/raw/train-labels-idx1-ubyte.gz
MNIST/raw/t10k-images-idx3-ubyte
MNIST/raw

In [5]:
datasets_names = ['CIFAR10', 'MNIST']
datasets_check = {'CIFAR10': (datasets.CIFAR10(root='cifar/', transform=transform, download=True, train=True),
                        datasets.CIFAR10(root='cifar/', transform=transform, download=True, train=False)),
            'MNIST': (datasets.MNIST(root = './', train=True, download=True, transform=transform),
                      datasets.MNIST(root = './', train=False, download=True, transform=transform))}

batch_sizes = list(product([64, 512], [64, 512]))

Files already downloaded and verified
Files already downloaded and verified


In [9]:
dataset_name = 'MNIST'
dataset_train, dataset_test = datasets_check[dataset_name]

print(dataset_name, 'WCLoss')

for N, M in batch_sizes:
    train_part1, train_part2 = divide_by_classes(dataset_train, N, cifar=False, stability_check=True)
    test_part1, test_part2 = divide_by_classes(dataset_train, M, cifar=False, stability_check=True)
    check_image = next(iter(train_part1))

    epochs = 500
    num_of_channels = check_image.size(1)
    image_size = check_image.size(2)

    discriminator = DiscriminatorMLP(image_size=image_size, num_of_channels=num_of_channels)
    if cuda:
        discriminator.cuda()

    trainer = Trainer(
        criterion=WCLoss(),
        train_part1=train_part1,
        train_part2=train_part2,
        test_part1=test_part1,
        test_part2=test_part2,
        discriminator=discriminator,
        weight_clipper=WeightClipper(0.08)
    )

    # training
    trainer.train(20, device, validate=False, verbose=False)

    # evaluation
    trainer.discriminator.eval()
    val_dest = []
    for i, (imgs1, imgs2) in tqdm(enumerate(zip(trainer.test_part1, trainer.test_part2))):
        
        imgs_m = imgs1.to(device, dtype=torch.float32)
        imgs_v = imgs2.to(device, dtype=torch.float32)

        phi = trainer.discriminator(imgs_m).view(-1)
        psi = trainer.discriminator(imgs_v).view(-1)

        if trainer.criterion.__class__.__name__ == 'WCLoss':
            d_est = -trainer.criterion(phi, psi) # WCLoss
        elif trainer.criterion.__class__.__name__ == 'GPLoss' or trainer.criterion.__class__.__name__ == 'LPLoss':
            d_est = -trainer.criterion(imgs_m, imgs_v, trainer.discriminator, phi, psi, device) # GPLoss
        elif trainer.criterion.__class__.__name__ == 'CLoss':
            d_est = -trainer.criterion(imgs_m, imgs_v, psi) # CLoss
        elif trainer.criterion.__class__.__name__ == 'CEpsilonLoss':
            d_est = -trainer.criterion(imgs_m, imgs_v, psi) - (trainer.criterion.ot_sink(imgs_m) + trainer.criterion.ot_sink(imgs_v)) / 2 # CEpsilonLoss

        val_dest.append(d_est.item())
    
    val_dest = np.array(val_dest)
    print(f'N = {N}, M = {M}: {np.round(val_dest.mean(), 2)} ± {np.round(val_dest.std(), 2)}')


MNIST WCLoss



N = 64, M = 64: 0.08 ± 0.01



N = 64, M = 512: 0.06 ± 0.0



N = 512, M = 64: 0.0 ± 0.0



N = 512, M = 512: 0.0 ± 0.0


In [10]:
dataset_name = 'MNIST'
dataset_train, dataset_test = datasets_check[dataset_name]

print(dataset_name, 'GPLoss')

for N, M in batch_sizes:
    train_part1, train_part2 = divide_by_classes(dataset_train, N, cifar=False, stability_check=True)
    test_part1, test_part2 = divide_by_classes(dataset_train, M, cifar=False, stability_check=True)
    check_image = next(iter(train_part1))

    epochs = 500
    num_of_channels = check_image.size(1)
    image_size = check_image.size(2)

    discriminator = DiscriminatorMLP(image_size=image_size, num_of_channels=num_of_channels)
    if cuda:
        discriminator.cuda()
    criterion = GPLoss(lambda_gp=10)
    criterion.optimizer_params['lr'] = 0.005
    trainer = Trainer(
        criterion=criterion,
        train_part1=train_part1,
        train_part2=train_part2,
        test_part1=test_part1,
        test_part2=test_part2,
        discriminator=discriminator
    )

    # training
    trainer.train(20, device, validate=False, verbose=False)

    # evaluation
    trainer.discriminator.eval()
    val_dest = []
    for i, (imgs1, imgs2) in tqdm(enumerate(zip(trainer.test_part1, trainer.test_part2))):
        
        imgs_m = imgs1.to(device, dtype=torch.float32)
        imgs_v = imgs2.to(device, dtype=torch.float32)

        phi = trainer.discriminator(imgs_m).view(-1)
        psi = trainer.discriminator(imgs_v).view(-1)

        if trainer.criterion.__class__.__name__ == 'WCLoss':
            d_est = -trainer.criterion(phi, psi) # WCLoss
        elif trainer.criterion.__class__.__name__ == 'GPLoss' or trainer.criterion.__class__.__name__ == 'LPLoss':
            d_est = -trainer.criterion(imgs_m, imgs_v, trainer.discriminator, phi, psi, device) # GPLoss
        elif trainer.criterion.__class__.__name__ == 'CLoss':
            d_est = -trainer.criterion(imgs_m, imgs_v, psi) # CLoss
        elif trainer.criterion.__class__.__name__ == 'CEpsilonLoss':
            d_est = -trainer.criterion(imgs_m, imgs_v, psi) - (trainer.criterion.ot_sink(imgs_m) + trainer.criterion.ot_sink(imgs_v)) / 2 # CEpsilonLoss

        val_dest.append(d_est.item())
    
    val_dest = np.array(val_dest)
    print(f'N = {N}, M = {M}: {np.round(val_dest.mean(), 2)} ± {np.round(val_dest.std(), 2)}')


MNIST GPLoss



N = 64, M = 64: -0.19 ± 0.01



N = 64, M = 512: -0.66 ± 0.0



N = 512, M = 64: -0.38 ± 0.01



N = 512, M = 512: -0.18 ± 0.0


In [11]:
dataset_name = 'MNIST'
dataset_train, dataset_test = datasets_check[dataset_name]

print(dataset_name, 'LPLoss')

for N, M in batch_sizes:
    train_part1, train_part2 = divide_by_classes(dataset_train, N, cifar=False, stability_check=True)
    test_part1, test_part2 = divide_by_classes(dataset_train, M, cifar=False, stability_check=True)
    check_image = next(iter(train_part1))

    epochs = 500
    num_of_channels = check_image.size(1)
    image_size = check_image.size(2)

    discriminator = DiscriminatorMLP(image_size=image_size, num_of_channels=num_of_channels)
    if cuda:
        discriminator.cuda()
    criterion = LPLoss(lambda_gp=10)
    criterion.optimizer_params['lr'] = 0.001
    trainer = Trainer(
        criterion=criterion,
        train_part1=train_part1,
        train_part2=train_part2,
        test_part1=test_part1,
        test_part2=test_part2,
        discriminator=discriminator
    )

    # training
    trainer.train(20, device, validate=False, verbose=False)

    # evaluation
    trainer.discriminator.eval()
    val_dest = []
    for i, (imgs1, imgs2) in tqdm(enumerate(zip(trainer.test_part1, trainer.test_part2))):
        
        imgs_m = imgs1.to(device, dtype=torch.float32)
        imgs_v = imgs2.to(device, dtype=torch.float32)

        phi = trainer.discriminator(imgs_m).view(-1)
        psi = trainer.discriminator(imgs_v).view(-1)

        if trainer.criterion.__class__.__name__ == 'WCLoss':
            d_est = -trainer.criterion(phi, psi) # WCLoss
        elif trainer.criterion.__class__.__name__ == 'GPLoss' or trainer.criterion.__class__.__name__ == 'LPLoss':
            d_est = -trainer.criterion(imgs_m, imgs_v, trainer.discriminator, phi, psi, device) # GPLoss
        elif trainer.criterion.__class__.__name__ == 'CLoss':
            d_est = -trainer.criterion(imgs_m, imgs_v, psi) # CLoss
        elif trainer.criterion.__class__.__name__ == 'CEpsilonLoss':
            d_est = -trainer.criterion(imgs_m, imgs_v, psi) - (trainer.criterion.ot_sink(imgs_m) + trainer.criterion.ot_sink(imgs_v)) / 2 # CEpsilonLoss

        val_dest.append(d_est.item())
    
    val_dest = np.array(val_dest)
    print(f'N = {N}, M = {M}: {np.round(val_dest.mean(), 2)} ± {np.round(val_dest.std(), 2)}')


MNIST LPLoss



N = 64, M = 64: 0.01 ± 0.0



N = 64, M = 512: 0.02 ± 0.0



N = 512, M = 64: 0.01 ± 0.0



N = 512, M = 512: 0.02 ± 0.0


In [12]:
dataset_name = 'MNIST'
dataset_train, dataset_test = datasets_check[dataset_name]

print(dataset_name, 'C-transform')

for N, M in batch_sizes:
    train_part1, train_part2 = divide_by_classes(dataset_train, N, cifar=False, stability_check=True)
    test_part1, test_part2 = divide_by_classes(dataset_train, M, cifar=False, stability_check=True)
    check_image = next(iter(train_part1))

    epochs = 500
    num_of_channels = check_image.size(1)
    image_size = check_image.size(2)

    discriminator = DiscriminatorMLP(image_size=image_size, num_of_channels=num_of_channels)
    if cuda:
        discriminator.cuda()
    criterion = CLoss()
    criterion.optimizer_params['lr'] = 0.001
    trainer = Trainer(
        criterion=criterion,
        train_part1=train_part1,
        train_part2=train_part2,
        test_part1=test_part1,
        test_part2=test_part2,
        discriminator=discriminator
    )

    # training
    trainer.train(20, device, validate=False, verbose=False)

    # evaluation
    trainer.discriminator.eval()
    val_dest = []
    for i, (imgs1, imgs2) in tqdm(enumerate(zip(trainer.test_part1, trainer.test_part2))):
        
        imgs_m = imgs1.to(device, dtype=torch.float32)
        imgs_v = imgs2.to(device, dtype=torch.float32)

        phi = trainer.discriminator(imgs_m).view(-1)
        psi = trainer.discriminator(imgs_v).view(-1)

        if trainer.criterion.__class__.__name__ == 'WCLoss':
            d_est = -trainer.criterion(phi, psi) # WCLoss
        elif trainer.criterion.__class__.__name__ == 'GPLoss' or trainer.criterion.__class__.__name__ == 'LPLoss':
            d_est = -trainer.criterion(imgs_m, imgs_v, trainer.discriminator, phi, psi, device) # GPLoss
        elif trainer.criterion.__class__.__name__ == 'CLoss':
            d_est = -trainer.criterion(imgs_m, imgs_v, psi) # CLoss
        elif trainer.criterion.__class__.__name__ == 'CEpsilonLoss':
            d_est = -trainer.criterion(imgs_m, imgs_v, psi) - (trainer.criterion.ot_sink(imgs_m) + trainer.criterion.ot_sink(imgs_v)) / 2 # CEpsilonLoss

        val_dest.append(d_est.item())
    
    val_dest = np.array(val_dest)
    print(f'N = {N}, M = {M}: {np.round(val_dest.mean(), 2)} ± {np.round(val_dest.std(), 2)}')


MNIST C-transform



N = 64, M = 64: 1.45 ± 0.05



N = 64, M = 512: 1.3 ± 0.0



N = 512, M = 64: 1.44 ± 0.06



N = 512, M = 512: 1.3 ± 0.0


In [13]:
dataset_name = 'MNIST'
dataset_train, dataset_test = datasets_check[dataset_name]

print(dataset_name, 'CEpsilon-transform')

for N, M in batch_sizes:
    train_part1, train_part2 = divide_by_classes(dataset_train, N, cifar=False, stability_check=True)
    test_part1, test_part2 = divide_by_classes(dataset_train, M, cifar=False, stability_check=True)
    check_image = next(iter(train_part1))

    epochs = 500
    num_of_channels = check_image.size(1)
    image_size = check_image.size(2)

    discriminator = DiscriminatorMLP(image_size=image_size, num_of_channels=num_of_channels)
    if cuda:
        discriminator.cuda()
    criterion = CEpsilonLoss(12)
    criterion.optimizer_params['lr'] = 0.0001
    trainer = Trainer(
        criterion=criterion,
        train_part1=train_part1,
        train_part2=train_part2,
        test_part1=test_part1,
        test_part2=test_part2,
        discriminator=discriminator
    )

    # training
    trainer.train(20, device, validate=False, verbose=False)

    # evaluation
    trainer.discriminator.eval()
    val_dest = []
    for i, (imgs1, imgs2) in tqdm(enumerate(zip(trainer.test_part1, trainer.test_part2))):
        
        imgs_m = imgs1.to(device, dtype=torch.float32)
        imgs_v = imgs2.to(device, dtype=torch.float32)

        phi = trainer.discriminator(imgs_m).view(-1)
        psi = trainer.discriminator(imgs_v).view(-1)

        if trainer.criterion.__class__.__name__ == 'WCLoss':
            d_est = -trainer.criterion(phi, psi) # WCLoss
        elif trainer.criterion.__class__.__name__ == 'GPLoss' or trainer.criterion.__class__.__name__ == 'LPLoss':
            d_est = -trainer.criterion(imgs_m, imgs_v, trainer.discriminator, phi, psi, device) # GPLoss
        elif trainer.criterion.__class__.__name__ == 'CLoss':
            d_est = -trainer.criterion(imgs_m, imgs_v, psi) # CLoss
        elif trainer.criterion.__class__.__name__ == 'CEpsilonLoss':
            d_est = -trainer.criterion(imgs_m, imgs_v, psi) - (trainer.criterion.ot_sink(imgs_m) + trainer.criterion.ot_sink(imgs_v)) / 2 # CEpsilonLoss

        val_dest.append(d_est.item())
    
    val_dest = np.array(val_dest)
    print(f'N = {N}, M = {M}: {np.round(val_dest.mean(), 2)} ± {np.round(val_dest.std(), 2)}')


MNIST CEpsilon-transform



N = 64, M = 64: 1.69 ± 0.04



N = 64, M = 512: 1.64 ± 0.0



N = 512, M = 64: 1.65 ± 0.03



N = 512, M = 512: 1.59 ± 0.0


In [ ]:
# MNIST
d_ground = get_gt_wass(train_part1.dataset, train_part2.dataset)
d_ground

In [14]:
dataset_name = 'CIFAR10'
dataset_train, dataset_test = datasets_check[dataset_name]

print(dataset_name, 'WCLoss')

for N, M in batch_sizes:
    train_part1, train_part2 = divide_by_classes(dataset_train, N, cifar=False, stability_check=True)
    test_part1, test_part2 = divide_by_classes(dataset_train, M, cifar=False, stability_check=True)
    check_image = next(iter(train_part1))

    epochs = 500
    num_of_channels = check_image.size(1)
    image_size = check_image.size(2)

    discriminator = DiscriminatorMLP(image_size=image_size, num_of_channels=num_of_channels)
    if cuda:
        discriminator.cuda()

    trainer = Trainer(
        criterion=WCLoss(),
        train_part1=train_part1,
        train_part2=train_part2,
        test_part1=test_part1,
        test_part2=test_part2,
        discriminator=discriminator,
        weight_clipper=WeightClipper(0.08)
    )

    # training
    trainer.train(20, device, validate=False, verbose=False)

    # evaluation
    trainer.discriminator.eval()
    val_dest = []
    for i, (imgs1, imgs2) in tqdm(enumerate(zip(trainer.test_part1, trainer.test_part2))):
        
        imgs_m = imgs1.to(device, dtype=torch.float32)
        imgs_v = imgs2.to(device, dtype=torch.float32)

        phi = trainer.discriminator(imgs_m).view(-1)
        psi = trainer.discriminator(imgs_v).view(-1)

        if trainer.criterion.__class__.__name__ == 'WCLoss':
            d_est = -trainer.criterion(phi, psi) # WCLoss
        elif trainer.criterion.__class__.__name__ == 'GPLoss' or trainer.criterion.__class__.__name__ == 'LPLoss':
            d_est = -trainer.criterion(imgs_m, imgs_v, trainer.discriminator, phi, psi, device) # GPLoss
        elif trainer.criterion.__class__.__name__ == 'CLoss':
            d_est = -trainer.criterion(imgs_m, imgs_v, psi) # CLoss
        elif trainer.criterion.__class__.__name__ == 'CEpsilonLoss':
            d_est = -trainer.criterion(imgs_m, imgs_v, psi) - (trainer.criterion.ot_sink(imgs_m) + trainer.criterion.ot_sink(imgs_v)) / 2 # CEpsilonLoss

        val_dest.append(d_est.item())
    
    val_dest = np.array(val_dest)
    print(f'N = {N}, M = {M}: {np.round(val_dest.mean(), 2)} ± {np.round(val_dest.std(), 2)}')


CIFAR10 WCLoss



N = 64, M = 64: 0.05 ± 0.01



N = 64, M = 512: 0.04 ± 0.0



N = 512, M = 64: 0.0 ± 0.0



N = 512, M = 512: 0.01 ± 0.0


In [16]:
dataset_name = 'CIFAR10'
dataset_train, dataset_test = datasets_check[dataset_name]

print(dataset_name, 'GPLoss')

for N, M in batch_sizes:
    train_part1, train_part2 = divide_by_classes(dataset_train, N, cifar=False, stability_check=True)
    test_part1, test_part2 = divide_by_classes(dataset_train, M, cifar=False, stability_check=True)
    check_image = next(iter(train_part1))

    epochs = 500
    num_of_channels = check_image.size(1)
    image_size = check_image.size(2)

    discriminator = DiscriminatorMLP(image_size=image_size, num_of_channels=num_of_channels)
    if cuda:
        discriminator.cuda()

    
    criterion = GPLoss(lambda_gp=10)
    criterion.optimizer_params['lr'] = 0.005

    trainer = Trainer(
        criterion=criterion,
        train_part1=train_part1,
        train_part2=train_part2,
        test_part1=test_part1,
        test_part2=test_part2,
        discriminator=discriminator
    )

    # training
    trainer.train(20, device, validate=False, verbose=False)

    # evaluation
    trainer.discriminator.eval()
    val_dest = []
    for i, (imgs1, imgs2) in tqdm(enumerate(zip(trainer.test_part1, trainer.test_part2))):
        
        imgs_m = imgs1.to(device, dtype=torch.float32)
        imgs_v = imgs2.to(device, dtype=torch.float32)

        phi = trainer.discriminator(imgs_m).view(-1)
        psi = trainer.discriminator(imgs_v).view(-1)

        if trainer.criterion.__class__.__name__ == 'WCLoss':
            d_est = -trainer.criterion(phi, psi) # WCLoss
        elif trainer.criterion.__class__.__name__ == 'GPLoss' or trainer.criterion.__class__.__name__ == 'LPLoss':
            d_est = -trainer.criterion(imgs_m, imgs_v, trainer.discriminator, phi, psi, device) # GPLoss
        elif trainer.criterion.__class__.__name__ == 'CLoss':
            d_est = -trainer.criterion(imgs_m, imgs_v, psi) # CLoss
        elif trainer.criterion.__class__.__name__ == 'CEpsilonLoss':
            d_est = -trainer.criterion(imgs_m, imgs_v, psi) - (trainer.criterion.ot_sink(imgs_m) + trainer.criterion.ot_sink(imgs_v)) / 2 # CEpsilonLoss

        val_dest.append(d_est.item())
    
    val_dest = np.array(val_dest)
    print(f'N = {N}, M = {M}: {np.round(val_dest.mean(), 2)} ± {np.round(val_dest.std(), 2)}')


CIFAR10 GPLoss



N = 64, M = 64: -0.74 ± 0.03



N = 64, M = 512: -0.14 ± 0.0



N = 512, M = 64: -0.6 ± 0.02



N = 512, M = 512: -2.9 ± 0.0


In [17]:
dataset_name = 'CIFAR10'
dataset_train, dataset_test = datasets_check[dataset_name]

print(dataset_name, 'LPLoss')

for N, M in batch_sizes:
    train_part1, train_part2 = divide_by_classes(dataset_train, N, cifar=False, stability_check=True)
    test_part1, test_part2 = divide_by_classes(dataset_train, M, cifar=False, stability_check=True)
    check_image = next(iter(train_part1))

    epochs = 500
    num_of_channels = check_image.size(1)
    image_size = check_image.size(2)

    discriminator = DiscriminatorMLP(image_size=image_size, num_of_channels=num_of_channels)
    if cuda:
        discriminator.cuda()

    
    criterion = LPLoss(lambda_gp=10)
    criterion.optimizer_params['lr'] = 0.001

    trainer = Trainer(
        criterion=criterion,
        train_part1=train_part1,
        train_part2=train_part2,
        test_part1=test_part1,
        test_part2=test_part2,
        discriminator=discriminator
    )

    # training
    trainer.train(20, device, validate=False, verbose=False)

    # evaluation
    trainer.discriminator.eval()
    val_dest = []
    for i, (imgs1, imgs2) in tqdm(enumerate(zip(trainer.test_part1, trainer.test_part2))):
        
        imgs_m = imgs1.to(device, dtype=torch.float32)
        imgs_v = imgs2.to(device, dtype=torch.float32)

        phi = trainer.discriminator(imgs_m).view(-1)
        psi = trainer.discriminator(imgs_v).view(-1)

        if trainer.criterion.__class__.__name__ == 'WCLoss':
            d_est = -trainer.criterion(phi, psi) # WCLoss
        elif trainer.criterion.__class__.__name__ == 'GPLoss' or trainer.criterion.__class__.__name__ == 'LPLoss':
            d_est = -trainer.criterion(imgs_m, imgs_v, trainer.discriminator, phi, psi, device) # GPLoss
        elif trainer.criterion.__class__.__name__ == 'CLoss':
            d_est = -trainer.criterion(imgs_m, imgs_v, psi) # CLoss
        elif trainer.criterion.__class__.__name__ == 'CEpsilonLoss':
            d_est = -trainer.criterion(imgs_m, imgs_v, psi) - (trainer.criterion.ot_sink(imgs_m) + trainer.criterion.ot_sink(imgs_v)) / 2 # CEpsilonLoss

        val_dest.append(d_est.item())
    
    val_dest = np.array(val_dest)
    print(f'N = {N}, M = {M}: {np.round(val_dest.mean(), 2)} ± {np.round(val_dest.std(), 2)}')


CIFAR10 LPLoss



N = 64, M = 64: 0.02 ± 0.01



N = 64, M = 512: -0.04 ± 0.0



N = 512, M = 64: 0.01 ± 0.01



N = 512, M = 512: 0.01 ± 0.0


In [18]:
dataset_name = 'CIFAR10'
dataset_train, dataset_test = datasets_check[dataset_name]

print(dataset_name, 'CLoss')

for N, M in batch_sizes:
    train_part1, train_part2 = divide_by_classes(dataset_train, N, cifar=False, stability_check=True)
    test_part1, test_part2 = divide_by_classes(dataset_train, M, cifar=False, stability_check=True)
    check_image = next(iter(train_part1))

    epochs = 500
    num_of_channels = check_image.size(1)
    image_size = check_image.size(2)

    discriminator = DiscriminatorMLP(image_size=image_size, num_of_channels=num_of_channels)
    if cuda:
        discriminator.cuda()

    
    criterion = CLoss()
    criterion.optimizer_params['lr'] = 0.001

    trainer = Trainer(
        criterion=criterion,
        train_part1=train_part1,
        train_part2=train_part2,
        test_part1=test_part1,
        test_part2=test_part2,
        discriminator=discriminator
    )

    # training
    trainer.train(20, device, validate=False, verbose=False)

    # evaluation
    trainer.discriminator.eval()
    val_dest = []
    for i, (imgs1, imgs2) in tqdm(enumerate(zip(trainer.test_part1, trainer.test_part2))):
        
        imgs_m = imgs1.to(device, dtype=torch.float32)
        imgs_v = imgs2.to(device, dtype=torch.float32)

        phi = trainer.discriminator(imgs_m).view(-1)
        psi = trainer.discriminator(imgs_v).view(-1)

        if trainer.criterion.__class__.__name__ == 'WCLoss':
            d_est = -trainer.criterion(phi, psi) # WCLoss
        elif trainer.criterion.__class__.__name__ == 'GPLoss' or trainer.criterion.__class__.__name__ == 'LPLoss':
            d_est = -trainer.criterion(imgs_m, imgs_v, trainer.discriminator, phi, psi, device) # GPLoss
        elif trainer.criterion.__class__.__name__ == 'CLoss':
            d_est = -trainer.criterion(imgs_m, imgs_v, psi) # CLoss
        elif trainer.criterion.__class__.__name__ == 'CEpsilonLoss':
            d_est = -trainer.criterion(imgs_m, imgs_v, psi) - (trainer.criterion.ot_sink(imgs_m) + trainer.criterion.ot_sink(imgs_v)) / 2 # CEpsilonLoss

        val_dest.append(d_est.item())
    
    val_dest = np.array(val_dest)
    print(f'N = {N}, M = {M}: {np.round(val_dest.mean(), 2)} ± {np.round(val_dest.std(), 2)}')


CIFAR10 CLoss



N = 64, M = 64: 7.21 ± 0.15



N = 64, M = 512: 6.49 ± 0.0



N = 512, M = 64: 6.98 ± 0.21



N = 512, M = 512: 6.3 ± 0.0


In [19]:
dataset_name = 'CIFAR10'
dataset_train, dataset_test = datasets_check[dataset_name]

print(dataset_name, 'CEpsilonLoss')

for N, M in batch_sizes:
    train_part1, train_part2 = divide_by_classes(dataset_train, N, cifar=False, stability_check=True)
    test_part1, test_part2 = divide_by_classes(dataset_train, M, cifar=False, stability_check=True)
    check_image = next(iter(train_part1))

    epochs = 500
    num_of_channels = check_image.size(1)
    image_size = check_image.size(2)

    discriminator = DiscriminatorMLP(image_size=image_size, num_of_channels=num_of_channels)
    if cuda:
        discriminator.cuda()

    
    criterion = CEpsilonLoss(1)
    criterion.optimizer_params['lr'] = 0.0001

    trainer = Trainer(
        criterion=criterion,
        train_part1=train_part1,
        train_part2=train_part2,
        test_part1=test_part1,
        test_part2=test_part2,
        discriminator=discriminator
    )

    # training
    trainer.train(20, device, validate=False, verbose=False)

    # evaluation
    trainer.discriminator.eval()
    val_dest = []
    for i, (imgs1, imgs2) in tqdm(enumerate(zip(trainer.test_part1, trainer.test_part2))):
        
        imgs_m = imgs1.to(device, dtype=torch.float32)
        imgs_v = imgs2.to(device, dtype=torch.float32)

        phi = trainer.discriminator(imgs_m).view(-1)
        psi = trainer.discriminator(imgs_v).view(-1)

        if trainer.criterion.__class__.__name__ == 'WCLoss':
            d_est = -trainer.criterion(phi, psi) # WCLoss
        elif trainer.criterion.__class__.__name__ == 'GPLoss' or trainer.criterion.__class__.__name__ == 'LPLoss':
            d_est = -trainer.criterion(imgs_m, imgs_v, trainer.discriminator, phi, psi, device) # GPLoss
        elif trainer.criterion.__class__.__name__ == 'CLoss':
            d_est = -trainer.criterion(imgs_m, imgs_v, psi) # CLoss
        elif trainer.criterion.__class__.__name__ == 'CEpsilonLoss':
            d_est = -trainer.criterion(imgs_m, imgs_v, psi) - (trainer.criterion.ot_sink(imgs_m) + trainer.criterion.ot_sink(imgs_v)) / 2 # CEpsilonLoss

        val_dest.append(d_est.item())
    
    val_dest = np.array(val_dest)
    print(f'N = {N}, M = {M}: {np.round(val_dest.mean(), 2)} ± {np.round(val_dest.std(), 2)}')


CIFAR10 CEpsilonLoss



N = 64, M = 64: 9.22 ± 0.09



N = 64, M = 512: 9.19 ± 0.0



N = 512, M = 64: 9.17 ± 0.17



N = 512, M = 512: 9.13 ± 0.0


In [15]:
# CIFAR-10
d_ground = get_gt_wass(train_part1.dataset, train_part2.dataset)
d_ground

6.892722478299294